# Modules to be imported

In [1]:
import re
import overpy
import psycopg2
import statistics
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import csv

# Working with the extracted data

In [2]:
#set option to see all rows
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

#open csv file from extracted immo entries
immos = []
with open('immo.csv', newline='') as csvfile:
    spamreader = csv.reader(csvfile, delimiter=' ', quotechar='|')
    for row in spamreader:
        print(' '.join(row).split(','))
        immos.append(' '.join(row))

['"(\'4.5 rooms', ' 112 m²', " CHF 3970.—'", " 'Ernst-Jung-Gasse 18", ' 8400 Winterthur', ' ZH\')"', '"(\'3.5 rooms', ' 96 m²', " CHF 1755.—'", " 'Römerstr. 152", ' 8404 Winterthur', ' ZH\')"', '"(\'3 rooms', ' 65 m²', " CHF 1480.—'", " 'Strahleggstrasse 68", ' 8400 Winterthur', ' ZH\')"', '"(\'3.5 rooms', ' 83 m²', " CHF 1920.—'", " 'Hegistr. 35d", ' 8404 Winterthur', ' ZH\')"', '"(\'2.5 rooms', ' 55 m²', " CHF 1770.—'", " 'Wülflingerstrasse 155", ' 8408 Winterthur', ' ZH\')"', '"(\'4.5 rooms', ' 105 m²', " CHF 1873.—'", " 'Landvogt-Waser-Strasse 33", ' 8405 Winterthur', ' ZH\')"', '"(\'1 room', ' 26 m²', " CHF 1195.—'", " 'Wartstr. 28", ' 8400 Winterthur', ' ZH\')"', '"(\'4.5 rooms', ' 171 m²', " CHF 3339.—'", " 'Stadthausstrasse 12", ' 8400 Winterthur', ' ZH\')"', '"(\'6.5 rooms', ' 200 m²', " CHF 4450.—'", " 'Schlosshofstrasse 218", ' 8404 Winterthur', ' ZH\')"', '"(\'3.5 rooms', ' 103 m²', " CHF 2420.—'", " 'Eichgutstr. 4", ' 8400 Winterthur', ' ZH\')"', '"(\'3 rooms', ' 70 m²', "

In [3]:
#create new dataframe and insert all the results
df = pd.DataFrame()
#do some string transformations and split the string into separate values
for i in immos:
    i = i.replace('"','').replace('\'','')
    i = re.split(r'[()]', i)
    i = [x for x in i if not(x=='' or x==',')]
    df1 = pd.DataFrame(i)
    df1 = df1[0].str.split(',', expand=True)
    df = pd.concat([df,df1])
   

In [4]:
#initial dataframe length without filters
len(df)

4786

In [5]:
# get only the data which has m^2 information
df = df[df[1].str.contains('m²')==True]
df = df.reset_index(inplace=False, drop=True)
df.head()

0        1            2                       3                 4  \
0  4.5 rooms   112 m²   CHF 3970.—     Ernst-Jung-Gasse 18   8400 Winterthur   
1  3.5 rooms    96 m²   CHF 1755.—           Römerstr. 152   8404 Winterthur   
2    3 rooms    65 m²   CHF 1480.—     Strahleggstrasse 68   8400 Winterthur   
3  3.5 rooms    83 m²   CHF 1920.—            Hegistr. 35d   8404 Winterthur   
4  2.5 rooms    55 m²   CHF 1770.—   Wülflingerstrasse 155   8408 Winterthur   

     5     6     7    8  
0   ZH  None  None  NaN  
1   ZH  None  None  NaN  
2   ZH  None  None  NaN  
3   ZH  None  None  NaN  
4   ZH  None  None  NaN

In [6]:
len(df)

3858

In [7]:
df = df.where(pd.notnull(df), None)

for i, rows in df.iterrows():
    #print(print(rows[4]))
    if(rows[4] is not None):
        if(re.match("[A-Z]{2}$",rows[4].lstrip())):
            #print(i)
            df[5][i] = df[4][i].lstrip()
        if(re.search(r"^\d{4}",rows[3].lstrip())):
            #print(i)
            df[4][i] = df[3][i].lstrip()
            df[3][i] = 'nicht vorhanden'
        if(re.search(r"\.\—",df[3][i])):
                if(re.search(r"^\d{4}",rows[4].lstrip())):
                    df[2][i] = df[2][i]+(df[3][i].lstrip())
                    df[3][i] = 'nicht vorhanden'
                    #print(i)
                elif(re.search(r"^\d{4}",rows[5].lstrip())):
                    df[2][i] = df[2][i]+(df[3][i].lstrip())
                    df[3][i] = df[4][i].lstrip()
                    df[4][i] = df[5][i].lstrip()
                    df[5][i] = df[6][i].lstrip()
                    df[6][i] = None
                    #df[3][i] = 'nicht vorhanden'

        if (rows[6] is not None):
            if(re.match("[A-Z]{2}$",rows[6].lstrip())):
                #print(i)
                df[4][i] = df[5][i].lstrip()
                df[5][i] = df[6][i].lstrip()
                df[6][i] = None
            elif(re.match(r"^\d{4}",rows[6].lstrip())):
                df[4][i] = df[6][i].lstrip()
                df[5][i] = df[7][i].lstrip()
                df[6][i] = None
                df[7][i] = None
                #print(df.iloc[i])
            elif(re.match(r"^\d{4}",rows[7].lstrip())):
                #df[5][i] = df[6][i].lstrip()
                df[4][i] = df[7][i].lstrip()
                df[5][i] = df[8][i].lstrip()
                df[6][i] = None
                df[7][i] = None
                df[8][i] = None
#   

In [8]:
df.head()

0        1            2                       3                 4  \
0  4.5 rooms   112 m²   CHF 3970.—     Ernst-Jung-Gasse 18   8400 Winterthur   
1  3.5 rooms    96 m²   CHF 1755.—           Römerstr. 152   8404 Winterthur   
2    3 rooms    65 m²   CHF 1480.—     Strahleggstrasse 68   8400 Winterthur   
3  3.5 rooms    83 m²   CHF 1920.—            Hegistr. 35d   8404 Winterthur   
4  2.5 rooms    55 m²   CHF 1770.—   Wülflingerstrasse 155   8408 Winterthur   

     5     6     7     8  
0   ZH  None  None  None  
1   ZH  None  None  None  
2   ZH  None  None  None  
3   ZH  None  None  None  
4   ZH  None  None  None

In [9]:
#check if every row has a zip code
import math
for i, rows in df.iterrows():
    if(rows[4] is  None):
        print(i)
        continue


1269
1829
1880
2281
2385
2515
3614


In [10]:
#manual data extension with the help of google
df.loc[1269][4] = '4052 Basel'
df.loc[1269][5] = 'BS'
df.loc[1829][4] = '4051 Basel'
df.loc[1829][5] = 'BS'
df = df.drop([1880])
df.loc[2261][4] = '1005 Lausanne'
df.loc[2281][4] = '1018 Lausanne'
df.loc[2281][5] = 'VD'
df.loc[2385][4] = '3013 Bern'
df.loc[2385][5] = 'BE'
df.loc[2515][4] = '3007 Bern'
df.loc[2515][5] = 'BE'
df.loc[3397][4] = '6992 Lugano'
df.loc[3614][4] = '2503 Biel/Bienne'
df.loc[3614][5] = 'BE'


In [11]:
df = df.drop(columns=[6,7,8])

In [12]:
# get only the data which has room information
df = df[df[0].str.contains('room')==True]
len(df)

3857

In [13]:
# get only the data which has correct price information
df = df[df[2].str.contains('CHF')==True]
len(df)

3821

In [14]:
#split rooms into number and word
df[0] = df[0].str.split()
df[1] = df[1].str.split()
df[2] = df[2].str.split()
df[4] = df[4].str.split()
df[6] = df[5]

In [15]:
df.head()

0          1              2                       3  \
0  [4.5, rooms]  [112, m²]  [CHF, 3970.—]     Ernst-Jung-Gasse 18   
1  [3.5, rooms]   [96, m²]  [CHF, 1755.—]           Römerstr. 152   
2    [3, rooms]   [65, m²]  [CHF, 1480.—]     Strahleggstrasse 68   
3  [3.5, rooms]   [83, m²]  [CHF, 1920.—]            Hegistr. 35d   
4  [2.5, rooms]   [55, m²]  [CHF, 1770.—]   Wülflingerstrasse 155   

                    4    5    6  
0  [8400, Winterthur]   ZH   ZH  
1  [8404, Winterthur]   ZH   ZH  
2  [8400, Winterthur]   ZH   ZH  
3  [8404, Winterthur]   ZH   ZH  
4  [8408, Winterthur]   ZH   ZH

In [16]:
#only save number of rooms, m2 value and francs and split zip code into two columns
for i,rows in df.iterrows():
    rows[0] = float(rows[0][0])
    rows[1] = int(rows[1][0])
    rows[2] = int(rows[2][1].replace('.—',''))
    rows[5] = str(rows[4][1])
    rows[4] = int(rows[4][0])
    

In [17]:
df.head()

0    1     2                       3     4           5    6
0  4.5  112  3970     Ernst-Jung-Gasse 18  8400  Winterthur   ZH
1  3.5   96  1755           Römerstr. 152  8404  Winterthur   ZH
2  3.0   65  1480     Strahleggstrasse 68  8400  Winterthur   ZH
3  3.5   83  1920            Hegistr. 35d  8404  Winterthur   ZH
4  2.5   55  1770   Wülflingerstrasse 155  8408  Winterthur   ZH

In [18]:
#create id
df.insert(0, 'ID', range(1, len(df)+1))

In [19]:
len(df)

3821

# WEB API using Overpass Turbo

In [20]:
# defining the overpass query
query = f'''
[out:json];
area[name="Zurich"] -> .searchArea0;
area[name="Geneva"] -> .searchArea1;
area[name="Basel"] -> .searchArea2;
area[name="Lausanne"] -> .searchArea3;
area[name="Bern"] -> .searchArea4;
area[name="Winterthur"] -> .searchArea5;
area[name="Luzern"] -> .searchArea6;
area[name="St. Gallen"] -> .searchArea7;
area[name="Lugano"] -> .searchArea8;
area[name="Biel"] -> .searchArea9;
( area.searchArea0; area.searchArea1; area.searchArea2; area.searchArea3; area.searchArea4; area.searchArea5; area.searchArea6; area.searchArea7; area.searchArea8; area.searchArea9;) -> .searchArea;
(node["shop"="supermarket"](area.searchArea);way["shop"="supermarket"](area.searchArea););
out center;
'''

# creating Overpass API object
api = overpy.Overpass()

# performing the query and retrieveing the results
response = api.query(query)

#create dataframe and append ways
rdf= pd.DataFrame()
for i in response.ways:
    if("addr:postcode" in i.tags and "name" in i.tags):
            tdf = pd.DataFrame(i.tags,index=[i.id])
            tdf["type"] = 'way'
            rdf = pd.concat([rdf,tdf])

#append nodes to the dataframe
for i in response.nodes:
    if("addr:postcode" in i.tags and "name" in i.tags):
        tdf = pd.DataFrame(i.tags,index=[i.id])
        tdf["type"] = 'node'
        rdf = pd.concat([rdf,tdf])


In [21]:
rdf.head()

addr:city addr:country addr:housenumber addr:postcode  \
22422728             Winterthur           CH                1          8400   
29199847            Emmenbrücke          NaN                1          6020   
41377377             Winterthur          NaN                9          8400   
46661880  Rommanle sur Lausanne           CH                2          1032   
46765109               Lausanne           CH               36          1007   

                 addr:street              alt_name      branch   brand  \
22422728        Bahnhofplatz  Coop City Winterthur  Winterthur    Coop   
29199847      Fichtenstrasse            Coop Emmen       Emmen    Coop   
41377377    Industriestrasse                   NaN         NaN    Aldi   
46661880  Route de Neuchâtel                   NaN         NaN     NaN   
46765109      Avenue de Cour                   NaN         NaN  Migros   

         brand:wikidata building building:levels height    name  \
22422728        Q432564   retail               5     26    Coop   
29199847        Q432564      yes               1    NaN    Coop   
41377377        Q125054   retail               1    NaN    Aldi   
46661880            NaN      yes             NaN    NaN  magbio   
46765109        Q680727      yes             NaN    NaN  Migros   

                              opening_hours             operator roof:levels  \
22422728  Mo-Sa 06:00-22:00; Su 08:00-20:00  Coop Genossenschaft           1   
29199847                                NaN  Coop Genossenschaft         NaN   
41377377          Mo-Sa 07:30-20:00; PH off                  NaN         NaN   
46661880                                NaN                  NaN         NaN   
46765109  Mo-Fr 07:30-19:00; Sa 07:30-18:00                  NaN         NaN   

         roof:shape         shop wheelchair type    brand:wikipedia  \
22422728       flat  supermarket        yes  way                NaN   
29199847       flat  supermarket        yes  way  de:Coop (Schweiz)   
41377377        NaN  supermarket        NaN  way            en:Aldi   
46661880        NaN  supermarket        NaN  way                NaN   
46765109        NaN  supermarket        NaN  way          en:Migros   

         building:roof                       url                 website  \
22422728           NaN                       NaN                     NaN   
29199847           NaN                       NaN                     NaN   
41377377          flat                       NaN                     NaN   
46661880           NaN  http://www.himalavie.ch/  https://www.magbio.ch/   
46765109           NaN                       NaN                     NaN   

           cash_withdrawal cash_withdrawal:fee  \
22422728               NaN                 NaN   
29199847               NaN                 NaN   
41377377               NaN                 NaN   
46661880               NaN                 NaN   
46765109  postfinance_card                  no   

         cash_withdrawal:purchase_required cash_withdrawal:type  \
22422728                               NaN                  NaN   
29199847                               NaN                  NaN   
41377377                               NaN                  NaN   
46661880                               NaN                  NaN   
46765109                                no             checkout   

              copyright oa:imported_by       oa:lat      oa:lon  \
22422728            NaN            NaN          NaN         NaN   
29199847            NaN            NaN          NaN         NaN   
41377377            NaN            NaN          NaN         NaN   
46661880            NaN            NaN          NaN         NaN   
46765109  OpenAddresses       sbrunner  46.51561737  6.61768007   

                  oa:version                             source  \
22422728                 NaN                                NaN   
29199847                 NaN                                NaN   
41377377                 N

# Open Data Swiss API fetching Einwohner Daten

In [22]:
import pprint
import requests     # 2.18.4
import json         # 2.0.9
import pandas as pd # 0.23.0

packages = 'https://opendata.swiss/api/3/action/package_list'

# Make the HTTP request
response = requests.get(packages)

# Use the json module to load CKAN's response into a dictionary
response_dict = json.loads(response.content)

# Check the contents of the response
assert response_dict['success'] is True  # make sure if response is OK
result = response_dict['result']         # extract all the packages from the response
pprint.pprint(result)        # pretty print the list to the screen

['__',
 '__101',
 '15-jahresverbrauch',
 '15-jahresverbrauch-ha',
 '1-personenhaushalte-anz',
 '2000-watt-areale',
 '2013-2020-gas-exchange-at-pfynwald',
 '2015-monitoring-geschaeftsliegenschaften',
 '2015-monitoring-landwirtschaft',
 '2015-monitoring-schulanlagen',
 '2015-monitoring-verwaltungsgebaeude',
 '2015-monitoring-wohnen',
 '2015-nachhaltigkeitsrosette-fondsvermoegen',
 '2015-nachhaltigkeitsrosette-geschaeftsliegenschaften',
 '2015-nachhaltigkeitsrosette-landwirtschaft',
 '2015-nachhaltigkeitsrosette-schulanlagen',
 '2015-nachhaltigkeitsrosette-verwaltungsgebaeude',
 '2015-nachhaltigkeitsrosette-verwaltungsvermoegen',
 '2015-nachhaltigkeitsrosette-wohnen',
 '2016-monitoring-eis-und-wasseranlagen',
 '2016-monitoring-geschaeftsliegeschaften',
 '2016-monitoring-schulanlagen',
 '2016-monitoring-sportanlagen',
 '2016-monitoring-verwaltungsgebaeude',
 '2016-monitoring-wohnen',
 '2016-nachhaltigkeitsrosette-eis-und-wasseranlagen',
 '2016-nachhaltigkeitsrosette-fondsvermoegen',
 '2016

In [23]:
package = 'bevoelkerung-pro-plz'

In [24]:
# Base url for package information. This is always the same.
base_url = 'https://opendata.swiss/api/3/action/package_show?id='

# Construct the url for the package of interest
package_information_url = base_url + package

# Make the HTTP request
package_information = requests.get(package_information_url)

# Use the json module to load CKAN's response into a dictionary
package_dict = json.loads(package_information.content)

# Check the contents of the response.
assert package_dict['success'] is True  # again make sure if response is OK
package_dict = package_dict['result']   # we only need the 'result' part from the dictionary
pprint.pprint(package_dict)             # pretty print the package information to screen

{'accrual_periodicity': 'http://publications.europa.eu/resource/authority/frequency/IRREG',
 'author': 'Die Schweizerische Post',
 'author_email': None,
 'contact_points': [{'email': 'opendata@post.ch',
                     'name': 'Kontaktstelle Open Data'}],
 'coverage': '',
 'creator_user_id': '082dec4d-1b01-4463-886e-6bb9e5b3a69a',
 'description': {'de': 'Die der Post bekannten Anzahl der Bevölkerung, '
                       'gegliedert nach Bevölkerungstyp, Postleitzahl und '
                       'Stichdatum, jeweils für die letzten zwölf Monate.',
                 'en': '',
                 'fr': '',
                 'it': ''},
 'display_name': {'de': 'Bevölkerung pro PLZ', 'en': '', 'fr': '', 'it': ''},
 'extras': [{'key': 'publishers',
             'value': '[{"label": "Die Schweizerische Post"}]'}],
 'groups': [{'description': {'de': '', 'en': '', 'fr': '', 'it': ''},
             'display_name': {'de': 'Verwaltung',
                              'en': 'Administration',
   

In [25]:
# Get the url for the data from the dictionary
data_url = package_dict['resources'][0]['url']
print('Data url:     ' + data_url)

# Print the data format
data_format = package_dict['resources'][0]['format']
print('Data format:  ' + data_format)

Data url:     https://swisspost.opendatasoft.com/api/v2/catalog/datasets/bevoelkerung_proplz/exports/json
Data format:  JSON


In [26]:
# List of formats we work with in this excercise
csv = ['comma-separated-values', 'CSV', 'csv']
tsv = ['tab-separated-values', 'TSV', 'tsv']
xls = ['XLS']
js = ['JSON']

# Download the data to a Pandas DataFrame. Use seperate function calls, depending on the format of the dataset.
if any(s in data_format for s in csv):     # pd.read_csv()
    ddf = pd.read_csv(data_url)
elif any(s in data_format for s in tsv):   # pd.read_csv() and specify the delimiter
    ddf = pd.read_csv(data_url, sep='\t')
elif any(s in data_format for s in xls):   # pd.read_excel()
    ddf = pd.read_excel(data_url)
elif any(s in data_format for s in js):   # pd.read_excel()
    ddf = pd.read_json(data_url)
else:
    print('Sorry, the data format is not supported for this exercise')

# Print the first rows to the screen to inspect the dataset    
ddf.head(5)

stichdatum     plz  anzahl typ         ortbez18
0  2023-05-01  4617.0     999   m          Gunzgen
1  2023-05-01  4618.0      55   f         Boningen
2  2023-05-01  4623.0    1292   w        Neuendorf
3  2023-05-01  4624.0    1055   m        Härkingen
4  2023-05-01  4626.0     132   f  Niederbuchsiten

In [27]:
orte = ['Zürich', 'Genève', 'Basel', 'Lausanne', 'Bern', 'Winterthur', 'Luzern', 'St. Gallen', 'Lugano', 'Biel']
df3 = pd.DataFrame(columns=['city','einwohner'])
for o in orte:
    df5 = ddf[ddf['ortbez18'].str.contains(o)==True]
    anzahl = df5.sum(axis=0)['anzahl']
    df3.loc[len(df3)] = [o,anzahl]

In [28]:
#create id
df3.insert(0, 'ID', range(1, len(df3)+1))

In [29]:

df3


ID        city  einwohner
0   1      Zürich     598357
1   2      Genève     291016
2   3       Basel     247700
3   4    Lausanne     237779
4   5        Bern     237332
5   6  Winterthur     151633
6   7      Luzern     118017
7   8  St. Gallen     109042
8   9      Lugano      66072
9  10        Biel      75153

# Connection to AWS PostgreSQL and inserting Data

In [30]:
conn = psycopg2.connect(
        host="ads-database1.cbwqb3cep5ch.eu-central-1.rds.amazonaws.com",
        database="adsdatabase",
        user="adschief1",
        password="1eYvmDnMPikKSImeLrev"
    )
cur = conn.cursor()

In [31]:
# Create the table for ImmoScout24 in the database
cur.execute(
    '''CREATE TABLE IF NOT EXISTS immos (
   "id" int PRIMARY KEY,
   "rooms" FLOAT NOT NULL,
   "size" INT NOT NULL,
   "price" INT NOT NULL,
   "address" VARCHAR ( 255 ),
   "zipcode" INT NOT NULL,
   "city"  VARCHAR ( 15 ) NOT NULL,
   "kanton" VARCHAR ( 2 ) NOT NULL
);'''
)

In [32]:
# Create the table for Overpass in the database
cur.execute(
    '''CREATE TABLE IF NOT EXISTS supermarkets (
   "id" BIGINT PRIMARY KEY,
   "type" VARCHAR ( 10 ) NOT NULL,
   "name" VARCHAR ( 255 ),
   "zipcode" INT NOT NULL,
   "city" VARCHAR ( 50 ) ,
   "address" VARCHAR ( 255 )
);'''
)

In [33]:
# Create the table for Open Data Swiss API in the database
cur.execute(
    '''CREATE TABLE IF NOT EXISTS opendataswiss (
    "id" INT PRIMARY KEY,
    "city" VARCHAR ( 25 ) NOT NULL,
    "einwohner" INT NOT NULL
    );'''
)

In [34]:
# Insert the data from ImmoScout24 into the database

# Iterate over the properties array
for i, rows in df.iterrows():
    
    # Extract the individual details
    id = rows["ID"]
    rooms = rows[0]
    size = rows[1]
    price = rows[2]
    address = rows[3]
    zipcode = rows[4]
    city = rows[5]
    kanton = rows[6].lstrip()
    
    # Process the individual data record as needed
    print("Rooms:", rooms)
    print("Size:", size)
    print("Price:", price)
    print("Address:", address)
    print("Zip-Code", zipcode)
    print("city", city)
    print("Kanton", kanton)
    print("--------------------")


    # Insert the data from ImmoScout24 into the database
    cur.execute(
        "INSERT INTO immos (id, rooms, size, price, address, zipcode, city, kanton) VALUES (%s, %s, %s, %s, %s, %s, %s, %s) on conflict do nothing",
        (id,rooms, size, price, address, zipcode, city, kanton)
    )


# Commit the changes to the database
conn.commit()

# Close the cursor and connection
#cur.close()
#conn.close()


Rooms: 4.5
Size: 112
Price: 3970
Address:  Ernst-Jung-Gasse 18
Zip-Code 8400
city Winterthur
Kanton ZH
--------------------
Rooms: 3.5
Size: 96
Price: 1755
Address:  Römerstr. 152
Zip-Code 8404
city Winterthur
Kanton ZH
--------------------
Rooms: 3.0
Size: 65
Price: 1480
Address:  Strahleggstrasse 68
Zip-Code 8400
city Winterthur
Kanton ZH
--------------------
Rooms: 3.5
Size: 83
Price: 1920
Address:  Hegistr. 35d
Zip-Code 8404
city Winterthur
Kanton ZH
--------------------
Rooms: 2.5
Size: 55
Price: 1770
Address:  Wülflingerstrasse 155
Zip-Code 8408
city Winterthur
Kanton ZH
--------------------
Rooms: 4.5
Size: 105
Price: 1873
Address:  Landvogt-Waser-Strasse 33
Zip-Code 8405
city Winterthur
Kanton ZH
--------------------
Rooms: 1.0
Size: 26
Price: 1195
Address:  Wartstr. 28
Zip-Code 8400
city Winterthur
Kanton ZH
--------------------
Rooms: 4.5
Size: 171
Price: 3339
Address:  Stadthausstrasse 12
Zip-Code 8400
city Winterthur
Kanton ZH
--------------------
Rooms: 6.5
Size: 200
Price

In [35]:
# Insert the data from Overpass into the database
for i, rows in rdf.iterrows():
    
    # Extract the individual details
    id = i
    type = rows["type"]
    name = rows["name"]
    address = str(rows["addr:street"])+' '+str(rows["addr:housenumber"])
    zipcode = rows["addr:postcode"]
    city = rows["addr:city"]


    # Process the individual data record as needed
    print("id:", id)
    print("type:", type)
    print("name:", name)
    print("Address:", address)
    print("Zip-Code", zipcode)
    print("city", city)
    print("--------------------")

    # Insert the data from Overpass into the database
    cur.execute(
        "INSERT INTO supermarkets (id, type, name, address, zipcode, city) VALUES (%s, %s, %s, %s, %s, %s) ON CONFLICT DO NOTHING",
        (id, type, name, address, zipcode, city)
    )
# Commit the changes to the database
conn.commit()

# Close the cursor and connection
#cur.close()
#conn.close()

id: 22422728
type: way
name: Coop
Address: Bahnhofplatz 1
Zip-Code 8400
city Winterthur
--------------------
id: 29199847
type: way
name: Coop
Address: Fichtenstrasse 1
Zip-Code 6020
city Emmenbrücke
--------------------
id: 41377377
type: way
name: Aldi
Address: Industriestrasse 9
Zip-Code 8400
city Winterthur
--------------------
id: 46661880
type: way
name: magbio
Address: Route de Neuchâtel 2
Zip-Code 1032
city Rommanle sur Lausanne
--------------------
id: 46765109
type: way
name: Migros
Address: Avenue de Cour 36
Zip-Code 1007
city Lausanne
--------------------
id: 47005107
type: way
name: SezaiMarket
Address: Route Aloys-Fauquez 62
Zip-Code 1018
city Lausanne
--------------------
id: 57725628
type: way
name: Coop
Address: Tösstalstrasse 236
Zip-Code 8405
city Winterthur
--------------------
id: 87220776
type: way
name: Migros
Address: Hertensteinstrasse 9
Zip-Code 6004
city Luzern
--------------------
id: 90520644
type: way
name: Denner
Address: Sälistrasse 21
Zip-Code 6005
city

cur = conn.cursor()
cur.execute('''DROP TABLE opendataswiss''')

In [36]:
# Insert the data from Open Data Swiss API into the database

# Iterate over the properties array
for i, rows in df3.iterrows():
    
    # Extract the individual details
    id = rows["ID"]
    city = rows["city"]
    einwohner = rows["einwohner"]
    
    # Process the individual data record as needed
    print("Ort:", city)
    print("Einwohner:", einwohner)
    print("--------------------")


    # Insert the data from Open Data Swiss API into the database
    cur.execute(
        "INSERT INTO opendataswiss (id, city, einwohner) VALUES (%s, %s, %s) on conflict do nothing",
        (id, city, einwohner)
    )


# Commit the changes to the database
conn.commit()

# Close the cursor and connection
#cur.close()
#conn.close()


Ort: Zürich
Einwohner: 598357
--------------------
Ort: Genève
Einwohner: 291016
--------------------
Ort: Basel
Einwohner: 247700
--------------------
Ort: Lausanne
Einwohner: 237779
--------------------
Ort: Bern
Einwohner: 237332
--------------------
Ort: Winterthur
Einwohner: 151633
--------------------
Ort: Luzern
Einwohner: 118017
--------------------
Ort: St. Gallen
Einwohner: 109042
--------------------
Ort: Lugano
Einwohner: 66072
--------------------
Ort: Biel
Einwohner: 75153
--------------------


In [37]:
query = "SELECT * FROM opendataswiss"
open_df = pd.read_sql(query, conn)
open_df.head()
len(open_df)

C:\Users\Snigis\AppData\Local\Temp\ipykernel_6880\1875380376.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  open_df = pd.read_sql(query, conn)


10

In [38]:
cur = conn.cursor()
cur.execute('''      
UPDATE immos
SET city = 'St.Gallen'
WHERE city = 'St.';
''')

#### Join the two Tables "immoscout24_data" and "overpass_data"

In [39]:
query = "SELECT * FROM immos"
immo_df = pd.read_sql(query, conn)
immo_df.head()

C:\Users\Snigis\AppData\Local\Temp\ipykernel_6880\1993057732.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  immo_df = pd.read_sql(query, conn)


id  rooms  size  price                 address  zipcode        city kanton
0   1    4.5   112   3970     Ernst-Jung-Gasse 18     8400  Winterthur     ZH
1   2    3.5    96   1755           Römerstr. 152     8404  Winterthur     ZH
2   3    3.0    65   1480     Strahleggstrasse 68     8400  Winterthur     ZH
3   4    3.5    83   1920            Hegistr. 35d     8404  Winterthur     ZH
4   5    2.5    55   1770   Wülflingerstrasse 155     8408  Winterthur     ZH

In [40]:
query = "SELECT * FROM supermarkets"
sm_df = pd.read_sql(query, conn)
sm_df.head()

C:\Users\Snigis\AppData\Local\Temp\ipykernel_6880\2095204900.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  sm_df = pd.read_sql(query, conn)


id type    name  zipcode                   city               address
0  22422728  way    Coop     8400             Winterthur        Bahnhofplatz 1
1  29199847  way    Coop     6020            Emmenbrücke      Fichtenstrasse 1
2  41377377  way    Aldi     8400             Winterthur    Industriestrasse 9
3  46661880  way  magbio     1032  Rommanle sur Lausanne  Route de Neuchâtel 2
4  46765109  way  Migros     1007               Lausanne     Avenue de Cour 36

In [41]:
query = "SELECT * FROM opendataswiss"
ods_df = pd.read_sql(query, conn)
ods_df.head()

C:\Users\Snigis\AppData\Local\Temp\ipykernel_6880\2633163449.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  ods_df = pd.read_sql(query, conn)


id      city  einwohner
0   1    Zürich     598357
1   2    Genève     291016
2   3     Basel     247700
3   4  Lausanne     237779
4   5      Bern     237332

In [42]:
immo_df.head()

id  rooms  size  price                 address  zipcode        city kanton
0   1    4.5   112   3970     Ernst-Jung-Gasse 18     8400  Winterthur     ZH
1   2    3.5    96   1755           Römerstr. 152     8404  Winterthur     ZH
2   3    3.0    65   1480     Strahleggstrasse 68     8400  Winterthur     ZH
3   4    3.5    83   1920            Hegistr. 35d     8404  Winterthur     ZH
4   5    2.5    55   1770   Wülflingerstrasse 155     8408  Winterthur     ZH

In [43]:
# get amount of markets per zip code
dupli = sm_df.pivot_table(index = ['zipcode'], aggfunc ='size')

In [44]:
dupli.head()

zipcode
1003    2
1004    3
1005    1
1006    1
1007    6
dtype: int64

In [45]:
# merge supermarket list with final dataset
final = immo_df.merge(dupli.rename('supermarkets'),on='zipcode',how='left')
final = final.fillna(0)

In [46]:
final.head()

id  rooms  size  price                 address  zipcode        city kanton  \
0   1    4.5   112   3970     Ernst-Jung-Gasse 18     8400  Winterthur     ZH   
1   2    3.5    96   1755           Römerstr. 152     8404  Winterthur     ZH   
2   3    3.0    65   1480     Strahleggstrasse 68     8400  Winterthur     ZH   
3   4    3.5    83   1920            Hegistr. 35d     8404  Winterthur     ZH   
4   5    2.5    55   1770   Wülflingerstrasse 155     8408  Winterthur     ZH   

   supermarkets  
0          17.0  
1           8.0  
2          17.0  
3           8.0  
4           1.0

In [47]:
# get amount of markets per zip code
einwohner = ods_df.pivot_table(index = ['city'], aggfunc ='sum')

In [52]:
# merge population list with final dataset
final_ods = final.merge(einwohner.rename("einwohner"),on='city',how='left')
final_ods = final.fillna(0)

TypeError: Index(...) must be called with a collection of some kind, 'einwohner' was passed

In [51]:
final_ods

id  rooms  size  price  \
0        1    4.5   112   3970   
1        2    3.5    96   1755   
2        3    3.0    65   1480   
3        4    3.5    83   1920   
4        5    2.5    55   1770   
5        6    4.5   105   1873   
6        7    1.0    26   1195   
7        8    4.5   171   3339   
8        9    6.5   200   4450   
9       10    3.5   103   2420   
10      11    3.0    70   2010   
11      12    1.5    41   1130   
12      13    2.5    63   2335   
13      14    2.5    56   1740   
14      15    3.5    96   2230   
15      16    5.5   143   3410   
16      17    3.5    93   2330   
17      18    2.5    68   1860   
18      19    3.5    71   1440   
19      20    5.5   120   3230   
20      21    2.5    58   1650   
21      22    3.5    96   2550   
22      23    2.5    82   2275   
23      24    1.0    39   1245   
24      25    1.0    30    960   
25      26    3.5    92   2080   
26      27    4.5   121   2500   
27      28    4.0    67   1650   
28      29    3.5    88   2650   
29      30    2.5    66   1535   
30      31    4.5   116   2400   
31      32    3.0    69   1560   
32      33    1.0    48   1430   
33      34    3.0    67   1715   
34      35    3.5    75   1725   
35      36    3.5    77   1945   
36      37    4.5   110   2250   
37      38    3.5   115   2430   
38      39    3.5    92   2070   
39      40    3.5   169   4200   
40      41    1.5    34   1150   
41      42    2.5    55   1395   
42      43    3.0    72   2030   
43      44    5.5   157   4685   
44      45    3.0    60   1350   
45      46    2.5    51   1715   
46      47    1.5    35    895   
47      48    3.5    87   1920   
48      49    2.5    61   1620   
49      50    5.5   130   2650   
50      51    5.5   153   4300   
51      52    3.5   103   2730   
52      53    2.5    69   2190   
53      54    3.0    74   1930   
54      55    3.5    85   2080   
55      56    3.0    58   1460   
56      57    3.5    93   2140   
57      58    4.5   100   2400   
58      59    2.5    55   2350   
59      60    3.5    60   1875   
60      61    1.0    15   1200   
61      62    1.0    18    995   
62      63    4.5   100   2720   
63      64    8.5   214   4730   
64      65    2.5    61   1730   
65      66    1.5    45   1570   
66      67    3.5   100   2280   
67      68    1.5    40   1490   
68      69    3.5   110   3000   
69      70    3.5    94   3150   
70      71    1.0    20   1400   
71      72    1.0    17   1420   
72      73    3.5   120   2520   
73      74    3.5   100   2750   
74      75    3.5   171   4250   
75      76    2.5    55   1850   
76      77    5.5   150   2400   
77      78    2.0    47   1770   
78      79    2.5    57   2385   
79      80    4.5   112   3360   
80      81    2.5    87   3400   
81      82    2.5    55   3400   
82      83    2.0    35   3300   
83      84    2.5    40   3300   
84      85    2.5    45   3300   
85      86    2.5    45   3300   
86      87    2.5    40   3300   
87      88    2.0    35   3300   
88      89    2.5    55   3400   
89      90    3.5    81   3300   
90      91    1.0    24   1770   
91      92    2.5    45   1800   
92      93    1.0    33   1230   
93      94    1.5    26   1820   
94      95    4.0    69   1444   
95      96    2.5    81   2260   
96      97    2.5   106   3380   
97      98    2.0    57   1650   
98      99    4.5    83   3965   
99     100    3.5   169   9000   
100    101    4.5   101   3880   
101    102    3.5    93   4240   
102    103    3.0    96   4390   
103    104    2.5    60   2290   
104    105    3.0    61   1730   
105    106    4.5   100   5400   
106    107    2.5    65   2990   
107    108    1.0    15   1200   
108    109    4.5   112   2868   
109    110    4.5   161   6550   
110    111    3.5   104   3640   
111    112    3.5    64   2000   
112    113    3.5    75   2390   
113    114    3.0    56   1359   
114    115    3.0    65   1580   
115    116    5.5   157   6280   
116    117    2.0    41   2450

# EDA using our data from PostgreSQL

In [ ]:
# Summary statistics
final.describe()

In [ ]:
# Examine the data types
final.dtypes

In [ ]:
# Count number of missing values
final.isnull().sum()

In [ ]:
# Retrieve the data from the database
cur.execute("SELECT price FROM immos")

# Fetch all the rows of the query result
rows = cur.fetchall()

# Extract the values from the rows
prices = [row[0] for row in rows]

# Calculate the mean
mean = statistics.mean(prices)

# Calculate the median
median = statistics.median(prices)

# Calculate the mode
mode = statistics.mode(prices)

# Calculate the variance
variance = statistics.variance(prices)

# Calculate the standard deviation
std_dev = statistics.stdev(prices)

# Print the results
print("Mean:", mean)
print("Median:", median)
print("Mode:", mode)
print("Variance:", variance)
print("Standard Deviation:", std_dev)

In [ ]:
# Histogram of apartment prices
plt.figure(figsize=(10, 6))
plt.hist(final['price'], bins=20, edgecolor='black')
plt.xlabel('Price')
plt.ylabel('Frequency')
plt.title('Distribution of Apartment Prices')
plt.show()

# Scatter plot of apartment price vs. square footage
plt.figure(figsize=(10, 6))
plt.scatter(final['size'], final['price'])
plt.xlabel('Square Footage')
plt.ylabel('Price')
plt.title('Apartment Price vs. Square Footage')
plt.show()

# Correlation Matrix 

### How do we separate the data into training and testing data?

In [ ]:
# Split the data into training and test sets (80% training, 20% testing)
train_df, test_df = train_test_split(final, test_size=0.2, random_state=42)


# Create the correlation matrix 
correlation_matrix = train_df.corr()

print(correlation_matrix)

### Correlation Matrix Plot

In [ ]:
# Correlation Matrix Plot (corrplot)
sns.pairplot(train_df)

# normalization standardization

In [ ]:
# Let us standardize training set, creating the so-called Z-scores.
train_df_mean = train_df.mean()
train_df_std = train_df.std()
train_df_stand = (train_df - train_df_mean)/train_df_std

# Let us do the same for the test dataset
test_df_mean = test_df.mean()
test_df_std = test_df.std()
test_df_stand = (test_df - test_df_mean)/test_df_std

print("The data points have been standardized.")

# Linear Regression

In [ ]:
# Create an empty list that will eventually hold all created feature columns.
feature_columns = []

resolution_in_Zs = 0.3  # 3/10 of a standard deviation.


# Create a bucket feature column for latitude.
rooms_as_a_numeric_column = tf.feature_column.numeric_column("rooms")
rooms_boundaries = list(np.arange(int(min(train_df_stand['rooms'])), 
                                     int(max(train_df_stand['rooms'])), 
                                     resolution_in_Zs))
rooms = tf.feature_column.bucketized_column(rooms_as_a_numeric_column, rooms_boundaries)

# Create a bucket feature column for longitude.
size_as_a_numeric_column = tf.feature_column.numeric_column("size")
size_boundaries = list(np.arange(int(min(train_df_stand['size'])), 
                                      int(max(train_df_stand['size'])), 
                                      resolution_in_Zs))
size = tf.feature_column.bucketized_column(size_as_a_numeric_column, size_boundaries)

# Create a feature cross of latitude and longitude.
rooms_x_size = tf.feature_column.crossed_column([rooms, size], hash_bucket_size=100)
crossed_feature = tf.feature_column.indicator_column(rooms_x_size)
feature_columns.append(crossed_feature)  

# Convert the list of feature columns into a layer that will later be fed into the model. 
my_feature_layer = tf.keras.layers.DenseFeatures(feature_columns)


In [ ]:
def create_model(my_learning_rate, feature_layer):
  """Create and compile a simple linear regression model."""
  # Most simple tf.keras models are sequential.
  model = tf.keras.models.Sequential()

  # Add the layer containing the feature columns to the model.
  model.add(feature_layer)

  # Add one linear layer to the model to yield a simple linear regressor.
  model.add(tf.keras.layers.Dense(units=1, input_shape=(1,)))

  # Construct the layers into a model that TensorFlow can execute.
  model.compile(optimizer=tf.keras.optimizers.experimental.RMSprop(learning_rate=my_learning_rate),
                loss="mean_squared_error",
                metrics=[tf.keras.metrics.MeanSquaredError()])

  return model           


def train_model(model, dataset, epochs, batch_size, target_name):
  """Feed a dataset into the model in order to train it."""

  # Split the dataset into features and label.
  features = {name:np.asarray(value).astype(np.float32) for name, value in dataset.items()}
  label = np.array(features.pop(target_name))
  history = model.fit(x=features, y=label, batch_size=batch_size,
                      epochs=epochs, shuffle=True)

  # Get details that will be useful for plotting the loss curve.
  epochs = history.epoch
  hist = pd.DataFrame(history.history)
  rmse = hist["mean_squared_error"]

  return epochs, rmse   

print("The create_model and the train_model functions are set.")

# Loss function

In [ ]:
def plot_the_loss_curve(epochs, mse):
  """Plot a curve of loss vs. epoch."""

  plt.figure()
  plt.xlabel("Epoch")
  plt.ylabel("Mean Squared Error")

  plt.plot(epochs, mse, label="Loss")
  plt.legend()
  plt.ylim([mse.min()*0.95, mse.max() * 1.05])
  plt.show()  

print("The plot_the_loss_curve function is correctly defined.")

In [ ]:
print(train_df_stand.dtypes)


In [ ]:
# The following variables are the hyperparameters.
learning_rate = 0.01 
epochs = 500 
batch_size = 300 

# Here we define the target.
target_name = "price"

# Establish the model's topography.
my_model = create_model(learning_rate, my_feature_layer)

# Train the model on the normalized training set.
epochs, mse = train_model(my_model, train_df_stand, epochs, batch_size, target_name)
plot_the_loss_curve(epochs, mse)

test_features = {name:np.asarray(value).astype(np.float32) for name, value in test_df_stand.items()}
test_label = np.array(test_features.pop(target_name)) # isolate the label
print("\n Evaluate the linear regression model against the test set:")
my_model.evaluate(x = test_features, y = test_label, batch_size=batch_size)

# NN

In [ ]:
def create_model(my_learning_rate, my_feature_layer):
  """Create and compile a simple network."""
  # Most simple tf.keras models are sequential.
  model = tf.keras.models.Sequential()

  # Add the layer containing the feature columns to the model.
  model.add(my_feature_layer)

  # Define the first hidden layer with 20 nodes.   
  model.add(tf.keras.layers.Dense(units=20, 
                                  activation='relu', 
                                  name='Hidden1'))
  
  # Define the second hidden layer with 10 nodes (i.e., 20/2). 
  model.add(tf.keras.layers.Dense(units=10, 
                                  activation='relu', 
                                  name='Hidden2'))
  
  # Define the output layer.
  model.add(tf.keras.layers.Dense(units=1,  
                                  name='Output'))                              
  
  model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=my_learning_rate),
                loss="mean_squared_error",
                metrics=[tf.keras.metrics.MeanSquaredError()])

  return model

In [ ]:
def train_model(model, dataset, epochs, target_name,
                batch_size=None):
  """Train the model by feeding it data."""

  # Split the dataset into features and label.
  features = {name:np.asarray(value).astype(np.float32) for name, value in dataset.items()}
  label = np.array(features.pop(target_name))
  history = model.fit(x=features, y=label, batch_size=batch_size,
                      epochs=epochs, shuffle=True) 

  # The list of epochs is stored separately from the rest of history.
  epochs = history.epoch
  
  # To track the progression of training, gather a snapshot of the model's mean squared error at each epoch. 
  hist = pd.DataFrame(history.history)
  mse = hist["mean_squared_error"]

  return epochs, mse

In [ ]:
# The following variables are the hyperparameters.
learning_rate = 0.01
epochs = 500
batch_size = 300

# Specify the label
target_name = "price"

# Establish the model's topography.
my_model = create_model(learning_rate, my_feature_layer)

# defined by the feature_layer.
epochs, mse = train_model(my_model, train_df_stand, epochs, 
                          target_name, batch_size)
plot_the_loss_curve(epochs, mse)

# After building a model against the training set, test that model
# against the test set.
test_features = {name:np.asarray(value).astype(np.float32) for name, value in test_df_stand.items()}
test_target = np.array(test_features.pop(target_name)) # isolate the target
print("\n Evaluate the new model against the test set:")
my_model.evaluate(x = test_features, y = test_target, batch_size=batch_size)

# Comparison

Assuming the convergence of both models, we can compare the test set loss for each. In our experiments, the loss of the linear regression was lower than that of the deep neural network (even if not dramatically lower), which suggests that the linear regression model will make better predictions than the deep neural network model.

However, we need to take into consideration model complexity, as well as other issues like explainability and the fact that the loss and MSE on both models are high (approx. 0.74) due to possibly lack of data or due to the quality of the data. 

If the market would be regulated, the linear regression would be preferred instead of the deep neural network.